In [1]:
from datetime import datetime

from binance.client import Client
from binance.enums import *

from coinmarketcapapi import CoinMarketCapAPI, CoinMarketCapAPIError

from datetime import datetime
from binance.helpers import round_step_size

import numpy as np
import pandas as pd
import json
import time
import sys


In [2]:
#client = Client('   ', '  ')

In [3]:
#cmc = CoinMarketCapAPI('  ')

In [4]:
#info = client.get_all_tickers()

In [5]:
#quote_ccy = 'USDT'

In [6]:
#ticker_list = [d['symbol'] for d in info if d['symbol'].endswith(quote_ccy)]

In [7]:
#rank_info = cmc.cryptocurrency_map(sort='cmc_rank').data

In [8]:
#target_rank_info = [d['symbol']+quote_ccy for d in rank_info if d['rank'] >= 100 and d['rank'] <= 500]

In [9]:
#target_ticker_list = [d for d in ticker_list if d in target_rank_info]

In [10]:
#target_ticker_list

In [11]:
#target_ticker_list = ['BONDUSDT']

In [12]:
global client;

In [13]:
global target_ticker_list

In [14]:
def init():
    global client
    client = Client('   ', '  ', {"verify": True, "timeout": 20})
    cmc = CoinMarketCapAPI('  ')
    info_all_tickers  = client.get_all_tickers()
    quote_ccy = 'USDT'
    ticker_list = [d['symbol'] for d in info_all_tickers if d['symbol'].endswith(quote_ccy)]
    rank_info = cmc.cryptocurrency_map(sort='cmc_rank').data
    target_rank_info = [d['symbol']+quote_ccy for d in rank_info if d['rank'] >= 100 and d['rank'] <= 500]
    global target_ticker_list
    target_ticker_list = [d for d in ticker_list if d in target_rank_info]
    target_ticker_list = ['BTCUSDT','ETHUSDT']
    return target_ticker_list
    

In [15]:
def is_candidate(filtered_klines_info): 
    is_candidate = False
    
    buy_kline_info = filtered_klines_info[0]
    buy_kline_average_volume = buy_kline_info[5]

    
    strong_context_kline_info = filtered_klines_info[1:len(filtered_klines_info)]


    
    strong_context_kline_average_volume = np.mean(strong_context_kline_info[:,5])
    
    for strong_context_kline in strong_context_kline_info:
        perc_change = strong_context_kline[-1]
        perc_volume = strong_context_kline[5] / buy_kline_average_volume

        if perc_change < -2 or perc_volume > 5:
            return False
        

        buy_line_open_price = buy_kline_info[1]
        buy_line_high_price = buy_kline_info[2]
        buy_line_low_price = buy_kline_info[3]
        buy_line_close_price = buy_kline_info[4]
        
        #Drop from high price to close price should be in the range of 10 - 15%
        drop_from_high_to_close_gate =   1.15 > buy_line_high_price/buy_line_close_price > 1.10

        
        
        #Percentage increase should be in the range of 7 - 15%
        percentage_gate = 100 > buy_kline_info[-1] > 1
        
        #The close price should not have dropped more than 15 % compared to Open Price
        
        mid_price_between_high_and_open_price = (buy_line_open_price + buy_line_high_price) / 2
        
        difference_between_high_and_open_price = buy_line_high_price - buy_line_open_price
        
        permissible_drop_between_open_close_price = (difference_between_high_and_open_price * 85) / 100
        drop_of_close_from_high_to_close_gate = (buy_line_close_price - buy_line_open_price) < permissible_drop_between_open_close_price
        


        if True and True and True:

            is_candidate = True
        else:
            is_candidate = False

        return is_candidate

In [16]:
def find_percentage_increase_or_decrease(focused_kline_array):
    percentage_value = []
    for kline in focused_kline_array:
        diff = kline[4] - kline[1]
        perc_diff = diff/kline[1]
        percentage_value.append(perc_diff*100)
    return percentage_value 

In [17]:
trade_list = []
init()
print('Total Tickers to Analyze')
print(len(target_ticker_list))
count = 1
retro_days = str(60)
for target_ticker in target_ticker_list:
    
    print('Analyzing Hourly Started ')
    print(target_ticker)

    #klines = client.get_historical_klines(target_ticker, Client.KLINE_INTERVAL_1HOUR, retro_days + " day ago UTC") 
    
    #with open(target_ticker + "file-" + retro_days + ".json", 'w') as f: 
            #json.dump(klines, f)
    

    with open(target_ticker + "file-" + retro_days + ".json", 'r') as f:
        klines = json.load(f)
    

    length = int(len(klines))
    print("****** Lenght *****")
    print(length)

    if(length < 24):
        continue
    
    klines.pop()
            
    

    array = np.array(klines, dtype=np.float64)
    focused_kline_array = np.delete(array, [6, 7, 8, 9, 10, 11], 1)
    percentage_value = find_percentage_increase_or_decrease(focused_kline_array)
    percentage_value = np.reshape(percentage_value, (length -1, 1))
    focused_kline_array = np.append(focused_kline_array, percentage_value, 1)
    
    focused_reverse_kline_array = focused_kline_array[::-1]

    for x in range(0, length):
        hit_ticker_dictionary = {}
        
        filtered_klines_info = focused_reverse_kline_array[x:x+5]


        if(len(filtered_klines_info) == 5):


            
            if(is_candidate(filtered_klines_info)):

                
                
                buy_kline_info = filtered_klines_info[0]

                
                hit_ticker_dictionary = {}
                buy_price = buy_kline_info[4]
                hit_ticker_dictionary['ticker'] = target_ticker
                hit_ticker_dictionary['buy_price'] = buy_kline_info[4]

                buy_timesstamp = buy_kline_info[0]
                hit_ticker_dictionary['buy_datetime'] = str(datetime.fromtimestamp(buy_timesstamp // 1000))
                
                proft_percentage = 1.10
                loss_percentage = 0.75
                profit_sell_price = buy_price * proft_percentage
                loss_sell_price = buy_price * loss_percentage
                
                
                
                usdt = 1000
                
                buy_quantity = usdt/buy_price
                hit_ticker_dictionary['quantity'] = buy_quantity
                
                
 
                
                for y in range(0, x) :
                    
                    start = x - (y + 1)
                    end = x - y
                    
                    high_price = focused_reverse_kline_array[start:end][0][2]
                    low_price = focused_reverse_kline_array[start:end][0][3]
                    close_price = focused_reverse_kline_array[start:end][0][4]
                    sell_timesstamp = focused_reverse_kline_array[start:end][0][0]
                    sell_datetime = str(datetime.fromtimestamp(sell_timesstamp // 1000))
                    
                    if high_price >= profit_sell_price:
                        hit_ticker_dictionary['sell_price'] = profit_sell_price

                        hit_ticker_dictionary['sell_datetime'] = str(datetime.fromtimestamp(sell_timesstamp // 1000))
                        difference = focused_reverse_kline_array[start:end][0][0] - buy_kline_info[0]
                        
                        hit_ticker_dictionary['days_to_gain_loss'] = round(difference/(1000 * 60 * 24 * 60))
                        price_difference = profit_sell_price - buy_price
                        hit_ticker_dictionary['price_diff'] = price_difference
                        hit_ticker_dictionary['proft_loss'] = usdt * proft_percentage - usdt
                        break
                    elif sell_timesstamp - buy_timesstamp >= 10200000 :
                        hit_ticker_dictionary['sell_price'] = close_price

                        hit_ticker_dictionary['sell_datetime'] = str(datetime.fromtimestamp(sell_timesstamp // 1000))
                        difference = focused_reverse_kline_array[start:end][0][0] - buy_kline_info[0]
                        
                        hit_ticker_dictionary['days_to_gain_loss'] = round(difference/(1000 * 60 * 24 * 60))
                        price_difference = close_price - buy_price
                        hit_ticker_dictionary['price_diff'] = price_difference
                        hit_ticker_dictionary['proft_loss'] = buy_quantity * close_price - buy_quantity * buy_price
                        break   
                        
                trade_list.append(hit_ticker_dictionary)        
                """
                
                for y in range(x+25, length):
                    high_price = focused_kline_array[y-1:y][0][2]
                    low_price = focused_kline_array[y-1:y][0][3]
                    close_price = focused_kline_array[y-1:y][0][4]
                    sell_timesstamp = focused_kline_array[y-1:y][0][0]
                    sell_datetime = str(datetime.fromtimestamp(sell_timesstamp // 1000))


                    if high_price >= profit_sell_price:
                        hit_ticker_dictionary['sell_price'] = profit_sell_price

                        hit_ticker_dictionary['sell_datetime'] = str(datetime.fromtimestamp(sell_timesstamp // 1000))
                        difference = focused_kline_array[y-1:y][0][0] - buy_kline_info[0]
                        
                        hit_ticker_dictionary['days_to_gain_loss'] = round(difference/(1000 * 60 * 24 * 60))
                        price_difference = profit_sell_price - buy_price
                        hit_ticker_dictionary['price_diff'] = price_difference
                        hit_ticker_dictionary['proft_loss'] = usdt * proft_percentage - usdt
                        
                        break
                        
                    elif low_price <= loss_sell_price and False:
                        hit_ticker_dictionary['sell_price'] = loss_sell_price

                        hit_ticker_dictionary['sell_datetime'] = str(datetime.fromtimestamp(sell_timesstamp // 1000))
                        difference = focused_kline_array[y-1:y][0][0] - buy_kline_info[0]
                        
                        hit_ticker_dictionary['days_to_gain_loss'] = round(difference/(1000 * 60 * 24 * 60))
                        price_difference = loss_sell_price - buy_price
                        hit_ticker_dictionary['price_diff'] = price_difference
                        hit_ticker_dictionary['proft_loss'] = usdt * loss_percentage - usdt
                        break
                    elif sell_timesstamp - buy_timesstamp >= 21600000 :
                        hit_ticker_dictionary['sell_price'] = close_price

                        hit_ticker_dictionary['sell_datetime'] = str(datetime.fromtimestamp(sell_timesstamp // 1000))
                        difference = focused_kline_array[y-1:y][0][0] - buy_kline_info[0]
                        
                        hit_ticker_dictionary['days_to_gain_loss'] = round(difference/(1000 * 60 * 24 * 60))
                        price_difference = close_price - buy_price
                        hit_ticker_dictionary['price_diff'] = price_difference
                        hit_ticker_dictionary['proft_loss'] = buy_quantity * close_price - buy_quantity * buy_price
                        break
                        
                        
                        
                        
                        
               
                
                busd = 100

                quantity = busd/ buy_kline_info[4]
                quantity_str = "{:0.0{}f}".format(quantity, 2)

               
                order = client.create_test_order(symbol=target_ticker, side=SIDE_BUY, type='MARKET', quoteOrderQty=busd)
                time.sleep(5)
                order_id = order['orderId'] 
                '''order_id = client.get_all_orders(symbol=target_ticker)[0]['orderId'] '''

                buy_price = order['fills'][0]['price']
                buy_qty = order['executedQty']
                sell_price = buy_price * 1.03



                while client.get_order(symbol=target_ticker, orderId=order_id)['status'] != 'FILLED':
                    time.sleep(10)

                if client.get_order(symbol=target_ticker, orderId=order_id)['status'] == 'FILLED':
                    asset = target_ticker.split("USDT")[0]
                    balance = client.get_asset_balance(asset=asset)
                    free_to_trade = balance['free']
                    sell_price_str = "{:0.0{}f}".format(sell_price, 2)

                    order = client.create_test_order(symbol=target_ticker, side=SIDE_SELL, type='LIMIT', quantity=float(balance['free']), price=sell_price_str, timeInForce=TIME_IN_FORCE_GTC)
                    print('********** SELL ORDER SET ************************')

                    """


Total Tickers to Analyze
2
Analyzing Hourly Started 
BTCUSDT
****** Lenght *****
1440
Analyzing Hourly Started 
ETHUSDT
****** Lenght *****
1440


In [18]:
trade_list

[{'ticker': 'BTCUSDT',
  'buy_price': 23341.12,
  'buy_datetime': '2022-08-03 15:00:00',
  'quantity': 0.04284284558752965},
 {'ticker': 'BTCUSDT',
  'buy_price': 23264.69,
  'buy_datetime': '2022-08-03 14:00:00',
  'quantity': 0.042983594451505694},
 {'ticker': 'BTCUSDT',
  'buy_price': 23402.83,
  'buy_datetime': '2022-08-03 13:00:00',
  'quantity': 0.0427298749766588},
 {'ticker': 'BTCUSDT',
  'buy_price': 23410.54,
  'buy_datetime': '2022-08-03 12:00:00',
  'quantity': 0.04271580236936012,
  'sell_price': 23341.12,
  'sell_datetime': '2022-08-03 15:00:00',
  'days_to_gain_loss': 0,
  'price_diff': -69.42000000000189,
  'proft_loss': -2.9653310004811146},
 {'ticker': 'BTCUSDT',
  'buy_price': 23383.55,
  'buy_datetime': '2022-08-03 11:00:00',
  'quantity': 0.04276510623921518,
  'sell_price': 23264.69,
  'sell_datetime': '2022-08-03 14:00:00',
  'days_to_gain_loss': 0,
  'price_diff': -118.86000000000058,
  'proft_loss': -5.0830605275931475},
 {'ticker': 'BTCUSDT',
  'buy_price': 23

In [19]:
a = 10
b = 5

step = -1 if a > b else 1
for x in range (a, b, step):
    print(x, end = ' ')

10 9 8 7 6 

In [20]:
len(trade_list)

2782

In [21]:
df = pd.DataFrame.from_dict(trade_list)

In [22]:
print('Profit and Loss')
df['proft_loss'].sum()

Profit and Loss


-978.0767330710422

In [48]:
df_pl = df[df['proft_loss'] > 0]

In [23]:
print('Number of Profit Trades')
df[df['price_diff'] > 0].shape[0]

Number of Profit Trades


1357

In [24]:
print('Number of Loss Trades')
df[df['price_diff'] < 0].shape[0]

Number of Loss Trades


1418

In [25]:
with pd.option_context('display.max_rows', None):
    display(df.sort_values('buy_datetime'))

ticker  buy_price         buy_datetime  quantity  sell_price  \
2781  ETHUSDT    1772.47  2022-06-04 21:00:00  0.564184    1798.860   
1402  BTCUSDT   29655.41  2022-06-04 21:00:00  0.033721   29808.010   
1401  BTCUSDT   29749.77  2022-06-04 22:00:00  0.033614   29864.040   
2780  ETHUSDT    1777.45  2022-06-04 22:00:00  0.562604    1804.580   
1400  BTCUSDT   29846.33  2022-06-04 23:00:00  0.033505   29740.640   
2779  ETHUSDT    1787.65  2022-06-04 23:00:00  0.559394    1798.220   
1399  BTCUSDT   29808.01  2022-06-05 00:00:00  0.033548   29691.740   
2778  ETHUSDT    1798.86  2022-06-05 00:00:00  0.555908    1786.140   
1398  BTCUSDT   29864.04  2022-06-05 01:00:00  0.033485   29793.990   
2777  ETHUSDT    1804.58  2022-06-05 01:00:00  0.554146    1793.610   
1397  BTCUSDT   29740.64  2022-06-05 02:00:00  0.033624   29766.950   
2776  ETHUSDT    1798.22  2022-06-05 02:00:00  0.556105    1793.850   
2775  ETHUSDT    1786.14  2022-06-05 03:00:00  0.559867    1790.290   
1396  BTCUSDT   29691.74  2022-06-05 03:00:00  0.033679   29722.900   
2774  ETHUSDT    1793.61  2022-06-05 04:00:00  0.557535    1797.470   
1395  BTCUSDT   29793.99  2022-06-05 04:00:00  0.033564   29793.950   
2773  ETHUSDT    1793.85  2022-06-05 05:00:00  0.557460    1791.240   
1394  BTCUSDT   29766.95  2022-06-05 05:00:00  0.033594   29729.710   
1393  BTCUSDT   29722.90  2022-06-05 06:00:00  0.033644   29645.670   
2772  ETHUSDT    1790.29  2022-06-05 06:00:00  0.558569    1785.820   
2771  ETHUSDT    1797.47  2022-06-05 07:00:00  0.556338    1788.900   
1392  BTCUSDT   29793.95  2022-06-05 07:00:00  0.033564   29691.810   
1391  BTCUSDT   29729.71  2022-06-05 08:00:00  0.033636   29639.460   
2770  ETHUSDT    1791.24  2022-06-05 08:00:00  0.558272    1781.900   
2769  ETHUSDT    1785.82  2022-06-05 09:00:00  0.559967    1780.860   
1390  BTCUSDT   29645.67  2022-06-05 09:00:00  0.033732   29641.650   
2768  ETHUSDT    1788.90  2022-06-05 10:00:00  0.559003    1788.200   
1389  BTCUSDT   29691.81  2022-06-05 10:00:00  0.033679   29718.690   
1388  BTCUSDT   29639.46  2022-06-05 11:00:00  0.033739   29717.990   
2767  ETHUSDT    1781.90  2022-06-05 11:00:00  0.561199    1790.700   
1387  BTCUSDT   29641.65  2022-06-05 12:00:00  0.033736   29656.460   
2766  ETHUSDT    1780.86  2022-06-05 12:00:00  0.561526    1784.150   
2765  ETHUSDT    1788.20  2022-06-05 13:00:00  0.559222    1795.340   
1386  BTCUSDT   29718.69  2022-06-05 13:00:00  0.033649   29791.710   
2764  ETHUSDT    1790.70  2022-06-05 14:00:00  0.558441    1811.410   
1385  BTCUSDT   29717.99  2022-06-05 14:00:00  0.033650   29972.220   
2763  ETHUSDT    1784.15  2022-06-05 15:00:00  0.560491    1800.800   
1384  BTCUSDT   29656.46  2022-06-05 15:00:00  0.033719   29866.940   
2762  ETHUSDT    1795.34  2022-06-05 16:00:00  0.556998    1824.560   
1383  BTCUSDT   29791.71  2022-06-05 16:00:00  0.033566   30021.990   
2761  ETHUSDT    1811.41  2022-06-05 17:00:00  0.552056    1816.150   
1382  BTCUSDT   29972.22  2022-06-05 17:00:00  0.033364   29996.310   
1381  BTCUSDT   29866.94  2022-06-05 18:00:00  0.033482   30049.860   
2760  ETHUSDT    1800.80  2022-06-05 18:00:00  0.555309    1821.210   
1380  BTCUSDT   30021.99  2022-06-05 19:00:00  0.033309   29945.840   
2759  ETHUSDT    1824.56  2022-06-05 19:00:00  0.548077    1810.770   
1379  BTCUSDT   29996.31  2022-06-05 20:00:00  0.033337   29965.230   
2758  ETHUSDT    1816.15  2022-06-05 20:00:00  0.550615    1813.170   
2757  ETHUSDT    1821.21  2022-06-05 21:00:00  0.549085    1815.580   
1378  BTCUSDT   30049.86  2022-06-05 21:00:00  0.033278   30022.670   
1377  BTCUSDT   29945.84  2022-06-05 22:00:00  0.033394   29919.210   
2756  ETHUSDT    1810.77  2022-06-05 22:00:00  0.552251    1806.230   
2755  ETHUSDT    1813.17  2022-06-05 23:00:00  0.551520    1836.000   
1376  BTCUSDT   29965.23  2022-06-05 23:00:00  0.033372   30301.700   
2754  ETHUSDT    1815.58  2022-06-06 00:00:00  0.550788    1864.040   
1375  BTCUSDT   30022.67  2022-

In [26]:
with pd.option_context('display.max_rows', None):
    display(df[df['price_diff'] > 0].sort_values('buy_datetime'))

ticker  buy_price         buy_datetime  quantity  sell_price  \
2781  ETHUSDT    1772.47  2022-06-04 21:00:00  0.564184    1798.860   
1402  BTCUSDT   29655.41  2022-06-04 21:00:00  0.033721   29808.010   
2780  ETHUSDT    1777.45  2022-06-04 22:00:00  0.562604    1804.580   
1401  BTCUSDT   29749.77  2022-06-04 22:00:00  0.033614   29864.040   
2779  ETHUSDT    1787.65  2022-06-04 23:00:00  0.559394    1798.220   
1397  BTCUSDT   29740.64  2022-06-05 02:00:00  0.033624   29766.950   
2775  ETHUSDT    1786.14  2022-06-05 03:00:00  0.559867    1790.290   
1396  BTCUSDT   29691.74  2022-06-05 03:00:00  0.033679   29722.900   
2774  ETHUSDT    1793.61  2022-06-05 04:00:00  0.557535    1797.470   
1389  BTCUSDT   29691.81  2022-06-05 10:00:00  0.033679   29718.690   
2767  ETHUSDT    1781.90  2022-06-05 11:00:00  0.561199    1790.700   
1388  BTCUSDT   29639.46  2022-06-05 11:00:00  0.033739   29717.990   
1387  BTCUSDT   29641.65  2022-06-05 12:00:00  0.033736   29656.460   
2766  ETHUSDT    1780.86  2022-06-05 12:00:00  0.561526    1784.150   
1386  BTCUSDT   29718.69  2022-06-05 13:00:00  0.033649   29791.710   
2765  ETHUSDT    1788.20  2022-06-05 13:00:00  0.559222    1795.340   
2764  ETHUSDT    1790.70  2022-06-05 14:00:00  0.558441    1811.410   
1385  BTCUSDT   29717.99  2022-06-05 14:00:00  0.033650   29972.220   
2763  ETHUSDT    1784.15  2022-06-05 15:00:00  0.560491    1800.800   
1384  BTCUSDT   29656.46  2022-06-05 15:00:00  0.033719   29866.940   
2762  ETHUSDT    1795.34  2022-06-05 16:00:00  0.556998    1824.560   
1383  BTCUSDT   29791.71  2022-06-05 16:00:00  0.033566   30021.990   
1382  BTCUSDT   29972.22  2022-06-05 17:00:00  0.033364   29996.310   
2761  ETHUSDT    1811.41  2022-06-05 17:00:00  0.552056    1816.150   
2760  ETHUSDT    1800.80  2022-06-05 18:00:00  0.555309    1821.210   
1381  BTCUSDT   29866.94  2022-06-05 18:00:00  0.033482   30049.860   
2755  ETHUSDT    1813.17  2022-06-05 23:00:00  0.551520    1836.000   
1376  BTCUSDT   29965.23  2022-06-05 23:00:00  0.033372   30301.700   
2754  ETHUSDT    1815.58  2022-06-06 00:00:00  0.550788    1864.040   
1375  BTCUSDT   30022.67  2022-06-06 00:00:00  0.033308   30844.070   
2753  ETHUSDT    1806.23  2022-06-06 01:00:00  0.553639    1867.200   
1374  BTCUSDT   29919.21  2022-06-06 01:00:00  0.033423   30926.110   
1373  BTCUSDT   30301.70  2022-06-06 02:00:00  0.033001   31251.000   
2752  ETHUSDT    1836.00  2022-06-06 02:00:00  0.544662    1878.290   
1372  BTCUSDT   30844.07  2022-06-06 03:00:00  0.032421   31222.910   
2751  ETHUSDT    1864.04  2022-06-06 03:00:00  0.536469    1880.390   
1371  BTCUSDT   30926.11  2022-06-06 04:00:00  0.032335   31169.050   
2750  ETHUSDT    1867.20  2022-06-06 04:00:00  0.535561    1870.390   
1370  BTCUSDT   31251.00  2022-06-06 05:00:00  0.031999   31274.230   
2749  ETHUSDT    1878.29  2022-06-06 05:00:00  0.532399    1886.100   
1369  BTCUSDT   31222.91  2022-06-06 06:00:00  0.032028   31292.770   
2748  ETHUSDT    1880.39  2022-06-06 06:00:00  0.531805    1893.770   
1368  BTCUSDT   31169.05  2022-06-06 07:00:00  0.032083   31469.280   
2747  ETHUSDT    1870.39  2022-06-06 07:00:00  0.534648    1905.270   
2746  ETHUSDT    1886.10  2022-06-06 08:00:00  0.530195    1911.430   
1367  BTCUSDT   31274.23  2022-06-06 08:00:00  0.031975   31475.140   
1366  BTCUSDT   31292.77  2022-06-06 09:00:00  0.031956   31483.190   
2745  ETHUSDT    1893.77  2022-06-06 09:00:00  0.528047    1908.460   
2744  ETHUSDT    1905.27  2022-06-06 10:00:00  0.524860    1909.550   
1362  BTCUSDT   31396.71  2022-06-06 13:00:00  0.031850   31506.690   
1361  BTCUSDT   31408.96  2022-06-06 14:00:00  0.031838   31541.420   
1357  BTCUSDT   31310.95  2022-06-06 18:00:00  0.031938   31470.720   
2736  ETHUSDT    1858.74  2022-06-06 18:00:00  0.537999    1863.830   
2735  ETHUSDT    1856.60  2022-06-06 19:00:00  0.538619    1861.960   
1356  BTCUSDT   31346.12  2022-06-06 19:00:00  0.031902   31462.490   
2734  ETHUSDT    1861.31  2022-

In [27]:
with pd.option_context('display.max_rows', None):
    display(df[df['price_diff'] < 0].sort_values('buy_datetime'))

ticker  buy_price         buy_datetime  quantity  sell_price  \
1400  BTCUSDT   29846.33  2022-06-04 23:00:00  0.033505    29740.64   
2778  ETHUSDT    1798.86  2022-06-05 00:00:00  0.555908     1786.14   
1399  BTCUSDT   29808.01  2022-06-05 00:00:00  0.033548    29691.74   
1398  BTCUSDT   29864.04  2022-06-05 01:00:00  0.033485    29793.99   
2777  ETHUSDT    1804.58  2022-06-05 01:00:00  0.554146     1793.61   
2776  ETHUSDT    1798.22  2022-06-05 02:00:00  0.556105     1793.85   
1395  BTCUSDT   29793.99  2022-06-05 04:00:00  0.033564    29793.95   
1394  BTCUSDT   29766.95  2022-06-05 05:00:00  0.033594    29729.71   
2773  ETHUSDT    1793.85  2022-06-05 05:00:00  0.557460     1791.24   
1393  BTCUSDT   29722.90  2022-06-05 06:00:00  0.033644    29645.67   
2772  ETHUSDT    1790.29  2022-06-05 06:00:00  0.558569     1785.82   
1392  BTCUSDT   29793.95  2022-06-05 07:00:00  0.033564    29691.81   
2771  ETHUSDT    1797.47  2022-06-05 07:00:00  0.556338     1788.90   
1391  BTCUSDT   29729.71  2022-06-05 08:00:00  0.033636    29639.46   
2770  ETHUSDT    1791.24  2022-06-05 08:00:00  0.558272     1781.90   
2769  ETHUSDT    1785.82  2022-06-05 09:00:00  0.559967     1780.86   
1390  BTCUSDT   29645.67  2022-06-05 09:00:00  0.033732    29641.65   
2768  ETHUSDT    1788.90  2022-06-05 10:00:00  0.559003     1788.20   
1380  BTCUSDT   30021.99  2022-06-05 19:00:00  0.033309    29945.84   
2759  ETHUSDT    1824.56  2022-06-05 19:00:00  0.548077     1810.77   
1379  BTCUSDT   29996.31  2022-06-05 20:00:00  0.033337    29965.23   
2758  ETHUSDT    1816.15  2022-06-05 20:00:00  0.550615     1813.17   
2757  ETHUSDT    1821.21  2022-06-05 21:00:00  0.549085     1815.58   
1378  BTCUSDT   30049.86  2022-06-05 21:00:00  0.033278    30022.67   
2756  ETHUSDT    1810.77  2022-06-05 22:00:00  0.552251     1806.23   
1377  BTCUSDT   29945.84  2022-06-05 22:00:00  0.033394    29919.21   
1365  BTCUSDT   31469.28  2022-06-06 10:00:00  0.031777    31396.71   
2743  ETHUSDT    1911.43  2022-06-06 11:00:00  0.523169     1909.72   
1364  BTCUSDT   31475.14  2022-06-06 11:00:00  0.031771    31408.96   
2742  ETHUSDT    1908.46  2022-06-06 12:00:00  0.523983     1904.77   
1363  BTCUSDT   31483.19  2022-06-06 12:00:00  0.031763    31442.96   
2741  ETHUSDT    1909.55  2022-06-06 13:00:00  0.523684     1893.97   
2740  ETHUSDT    1909.72  2022-06-06 14:00:00  0.523637     1886.79   
2739  ETHUSDT    1904.77  2022-06-06 15:00:00  0.524998     1858.74   
1360  BTCUSDT   31442.96  2022-06-06 15:00:00  0.031804    31310.95   
2738  ETHUSDT    1893.97  2022-06-06 16:00:00  0.527991     1856.60   
1359  BTCUSDT   31506.69  2022-06-06 16:00:00  0.031739    31346.12   
2737  ETHUSDT    1886.79  2022-06-06 17:00:00  0.530001     1861.31   
1358  BTCUSDT   31541.42  2022-06-06 17:00:00  0.031704    31349.50   
1354  BTCUSDT   31470.72  2022-06-06 21:00:00  0.031776    31395.55   
2733  ETHUSDT    1863.83  2022-06-06 21:00:00  0.536530     1855.30   
1353  BTCUSDT   31462.49  2022-06-06 22:00:00  0.031784    31373.10   
2732  ETHUSDT    1861.96  2022-06-06 22:00:00  0.537068     1859.84   
1352  BTCUSDT   31488.86  2022-06-06 23:00:00  0.031757    30197.77   
2731  ETHUSDT    1873.16  2022-06-06 23:00:00  0.533857     1758.79   
1351  BTCUSDT   31395.55  2022-06-07 00:00:00  0.031852    29568.47   
2730  ETHUSDT    1855.30  2022-06-07 00:00:00  0.538996     1742.46   
1350  BTCUSDT   31373.10  2022-06-07 01:00:00  0.031874    29402.08   
2729  ETHUSDT    1859.84  2022-06-07 01:00:00  0.537681     1740.95   
1349  BTCUSDT   30197.77  2022-06-07 02:00:00  0.033115    29563.62   
2728  ETHUSDT    1758.79  2022-06-07 02:00:00  0.568573     1756.75   
2726  ETHUSDT    1756.75  2022-06-07 05:00:00  0.569233     1755.80   
1348  BTCUSDT   29563.62  2022-06-07 05:00:00  0.033825    29521.24   
2721  ETHUSDT    1770.45  2022-06-07 10:00:00  0.564828     1753.69   
1343  BTCUSDT   29652.76  2022-06-07 10:00:00  0.033724    29521.50   
1342  BTCUSDT   29561.54  2022-

In [28]:
with pd.option_context('display.max_rows', None):
    display(df[pd.isna(df['sell_price'])].sort_values('buy_datetime'))

ticker  buy_price         buy_datetime  quantity  sell_price  \
2     BTCUSDT   23402.83  2022-08-03 13:00:00  0.042730         NaN   
1405  ETHUSDT    1665.54  2022-08-03 13:00:00  0.600406         NaN   
1     BTCUSDT   23264.69  2022-08-03 14:00:00  0.042984         NaN   
1404  ETHUSDT    1654.43  2022-08-03 14:00:00  0.604438         NaN   
0     BTCUSDT   23341.12  2022-08-03 15:00:00  0.042843         NaN   
1403  ETHUSDT    1663.53  2022-08-03 15:00:00  0.601131         NaN   

     sell_datetime  days_to_gain_loss  price_diff  proft_loss  
2              NaN                NaN         NaN         NaN  
1405           NaN                NaN         NaN         NaN  
1              NaN                NaN         NaN         NaN  
1404           NaN                NaN         NaN         NaN  
0              NaN                NaN         NaN         NaN  
1403           NaN                NaN         NaN         NaN

In [29]:
with pd.option_context('display.max_rows', None):
    display(df[np.invert(pd.isna(df['sell_price']))].sort_values('buy_datetime'))

ticker  buy_price         buy_datetime  quantity  sell_price  \
2781  ETHUSDT    1772.47  2022-06-04 21:00:00  0.564184    1798.860   
1402  BTCUSDT   29655.41  2022-06-04 21:00:00  0.033721   29808.010   
1401  BTCUSDT   29749.77  2022-06-04 22:00:00  0.033614   29864.040   
2780  ETHUSDT    1777.45  2022-06-04 22:00:00  0.562604    1804.580   
1400  BTCUSDT   29846.33  2022-06-04 23:00:00  0.033505   29740.640   
2779  ETHUSDT    1787.65  2022-06-04 23:00:00  0.559394    1798.220   
1399  BTCUSDT   29808.01  2022-06-05 00:00:00  0.033548   29691.740   
2778  ETHUSDT    1798.86  2022-06-05 00:00:00  0.555908    1786.140   
1398  BTCUSDT   29864.04  2022-06-05 01:00:00  0.033485   29793.990   
2777  ETHUSDT    1804.58  2022-06-05 01:00:00  0.554146    1793.610   
1397  BTCUSDT   29740.64  2022-06-05 02:00:00  0.033624   29766.950   
2776  ETHUSDT    1798.22  2022-06-05 02:00:00  0.556105    1793.850   
2775  ETHUSDT    1786.14  2022-06-05 03:00:00  0.559867    1790.290   
1396  BTCUSDT   29691.74  2022-06-05 03:00:00  0.033679   29722.900   
2774  ETHUSDT    1793.61  2022-06-05 04:00:00  0.557535    1797.470   
1395  BTCUSDT   29793.99  2022-06-05 04:00:00  0.033564   29793.950   
2773  ETHUSDT    1793.85  2022-06-05 05:00:00  0.557460    1791.240   
1394  BTCUSDT   29766.95  2022-06-05 05:00:00  0.033594   29729.710   
1393  BTCUSDT   29722.90  2022-06-05 06:00:00  0.033644   29645.670   
2772  ETHUSDT    1790.29  2022-06-05 06:00:00  0.558569    1785.820   
2771  ETHUSDT    1797.47  2022-06-05 07:00:00  0.556338    1788.900   
1392  BTCUSDT   29793.95  2022-06-05 07:00:00  0.033564   29691.810   
1391  BTCUSDT   29729.71  2022-06-05 08:00:00  0.033636   29639.460   
2770  ETHUSDT    1791.24  2022-06-05 08:00:00  0.558272    1781.900   
2769  ETHUSDT    1785.82  2022-06-05 09:00:00  0.559967    1780.860   
1390  BTCUSDT   29645.67  2022-06-05 09:00:00  0.033732   29641.650   
2768  ETHUSDT    1788.90  2022-06-05 10:00:00  0.559003    1788.200   
1389  BTCUSDT   29691.81  2022-06-05 10:00:00  0.033679   29718.690   
1388  BTCUSDT   29639.46  2022-06-05 11:00:00  0.033739   29717.990   
2767  ETHUSDT    1781.90  2022-06-05 11:00:00  0.561199    1790.700   
1387  BTCUSDT   29641.65  2022-06-05 12:00:00  0.033736   29656.460   
2766  ETHUSDT    1780.86  2022-06-05 12:00:00  0.561526    1784.150   
2765  ETHUSDT    1788.20  2022-06-05 13:00:00  0.559222    1795.340   
1386  BTCUSDT   29718.69  2022-06-05 13:00:00  0.033649   29791.710   
2764  ETHUSDT    1790.70  2022-06-05 14:00:00  0.558441    1811.410   
1385  BTCUSDT   29717.99  2022-06-05 14:00:00  0.033650   29972.220   
2763  ETHUSDT    1784.15  2022-06-05 15:00:00  0.560491    1800.800   
1384  BTCUSDT   29656.46  2022-06-05 15:00:00  0.033719   29866.940   
2762  ETHUSDT    1795.34  2022-06-05 16:00:00  0.556998    1824.560   
1383  BTCUSDT   29791.71  2022-06-05 16:00:00  0.033566   30021.990   
2761  ETHUSDT    1811.41  2022-06-05 17:00:00  0.552056    1816.150   
1382  BTCUSDT   29972.22  2022-06-05 17:00:00  0.033364   29996.310   
1381  BTCUSDT   29866.94  2022-06-05 18:00:00  0.033482   30049.860   
2760  ETHUSDT    1800.80  2022-06-05 18:00:00  0.555309    1821.210   
1380  BTCUSDT   30021.99  2022-06-05 19:00:00  0.033309   29945.840   
2759  ETHUSDT    1824.56  2022-06-05 19:00:00  0.548077    1810.770   
1379  BTCUSDT   29996.31  2022-06-05 20:00:00  0.033337   29965.230   
2758  ETHUSDT    1816.15  2022-06-05 20:00:00  0.550615    1813.170   
2757  ETHUSDT    1821.21  2022-06-05 21:00:00  0.549085    1815.580   
1378  BTCUSDT   30049.86  2022-06-05 21:00:00  0.033278   30022.670   
1377  BTCUSDT   29945.84  2022-06-05 22:00:00  0.033394   29919.210   
2756  ETHUSDT    1810.77  2022-06-05 22:00:00  0.552251    1806.230   
2755  ETHUSDT    1813.17  2022-06-05 23:00:00  0.551520    1836.000   
1376  BTCUSDT   29965.23  2022-06-05 23:00:00  0.033372   30301.700   
2754  ETHUSDT    1815.58  2022-06-06 00:00:00  0.550788    1864.040   
1375  BTCUSDT   30022.67  2022-

In [30]:
info = client.get_symbol_info('FLMUSDT')
print(info['filters'])

[{'filterType': 'PRICE_FILTER', 'minPrice': '0.00010000', 'maxPrice': '1000.00000000', 'tickSize': '0.00010000'}, {'filterType': 'PERCENT_PRICE', 'multiplierUp': '5', 'multiplierDown': '0.2', 'avgPriceMins': 5}, {'filterType': 'LOT_SIZE', 'minQty': '1.00000000', 'maxQty': '900000.00000000', 'stepSize': '1.00000000'}, {'filterType': 'MIN_NOTIONAL', 'minNotional': '10.00000000', 'applyToMarket': True, 'avgPriceMins': 5}, {'filterType': 'ICEBERG_PARTS', 'limit': 10}, {'filterType': 'MARKET_LOT_SIZE', 'minQty': '0.00000000', 'maxQty': '1321601.82638888', 'stepSize': '0.00000000'}, {'filterType': 'TRAILING_DELTA', 'minTrailingAboveDelta': 10, 'maxTrailingAboveDelta': 2000, 'minTrailingBelowDelta': 10, 'maxTrailingBelowDelta': 2000}, {'filterType': 'MAX_NUM_ORDERS', 'maxNumOrders': 200}, {'filterType': 'MAX_NUM_ALGO_ORDERS', 'maxNumAlgoOrders': 5}]


In [31]:
print(info['filters'][0]['tickSize'])

0.00010000


In [32]:
symbol_info = {}
def get_symbol_info(symbols):
    global symbol_info
    for symbol in symbols:
        info = client.get_symbol_info(symbol)
        base_asset = info['baseAsset']
#  PRICE_FILTER
        price_filter_min_quantity = float(info['filters'][0]['minPrice'])
        price_filter_max_quantity = float(info['filters'][0]['maxPrice'])
        price_filter_tick_size = float(info['filters'][0]['tickSize'])
        
#  LOT_SIZE (for market- and limit orders)
        lot_size_min_quantity = float(info['filters'][2]['minQty'])
        lot_size_max_quantity = float(info['filters'][2]['maxQty'])
        lot_size_step_size = float(info['filters'][2]['stepSize'])
        
#  MIN NOTIONAL
        min_notional = float(info['filters'][3]['minNotional'])
        symbol_info[symbol] = {'price_filter_min_quantity': price_filter_min_quantity, 'price_filter_max_quantity': price_filter_max_quantity,\
                               'price_filter_tick_size': price_filter_tick_size,'lot_size_min_quantity': lot_size_min_quantity, \
                                'lot_size_min_quantity': lot_size_min_quantity, 'lot_size_max_quantity': lot_size_max_quantity, \
                               'lot_size_step_size': lot_size_step_size, 'min_notional': min_notional, }
        
